Here we only need the data to scrap website + _Pandas_
- Nombre del tecnológico
- Estado
- Clave oficial
- Modalidad (Escolarizada / No escolarizada)
- Grado que otorga
- Carreras y módulos de especialidad
- url of the website / tecnológico

**Consultas que debe permitir el sistema**

¿Qué tecnológicos ofrecen la modalidad no escolarizada?

¿Qué tecnológicos comparten la misma carrera?

¿Cuántos tecnológicos son de tipo federal o estatal?

¿Cuáles son los módulos de especialidad disponibles por carrera (solo el nombre)?

In [33]:
from bs4 import BeautifulSoup
import requests
import pandas as pd

In [34]:
url = 'https://www.tecnm.mx/?vista=Licenciaturas'

page = requests.get(url)

soup = BeautifulSoup(page.text, 'html.parser')


In [35]:
print(soup)

<!DOCTYPE html>

<html lang="es-MX">
<head>
<!-- Accesibilidad -->
<link href="https://framework-gb.cdn.gob.mx/gm/accesibilidad/css/gobmx-accesibilidad.min.css" rel="stylesheet"/>
<title>TecNM | Tecnológico Nacional de México</title>
<meta charset="utf-8"/>
<meta content="TecNM" name="author"/>
<meta content="Página del Tecnológico Nacional de México" name="description"/>
<meta content="TecNM, Instituto Tecnológico Nacional de México, Tec, Tecnológico Nacional de México, Universidad" name="keywords">
<meta content="width=device-width, initial-scale=1, minimum-scale=1" name="viewport"/>
<meta content="TecNM" name="copyright">
<meta content="ALL" name="robots"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<link href="img/tecnmicono.ico" rel="icon">
<link href="assets/web/assets/mobirise-icons/mobirise-icons.css" rel="stylesheet"/>
<link href="assets/bootstrap/css/bootstrap-grid.min.css" rel="stylesheet"/>
<link href="assets/bootstrap/css/bootstrap-reboot.min.css" rel="styleshe

In [36]:
pageData = soup.find_all('div', class_='contenedor')


In [37]:
print(pageData)

[<div class="contenedor">
<div class="col-12 tz-gallery mx-auto text-center">
<img alt="" class="img-fluid w-80" src="vistas/escolares/convocatorias_ingreso/plantillas/banner_licenciaturasv3.jpg">
</img></div>
<br/><br/>
<div id="oferta-wrap">
<div id="oferta-header">
<input id="search" placeholder="Buscar por estado, plantel o carrera…" type="search"/>
<div id="toggles">
<button class="btn" id="expand-all">Expandir todo</button>
<button class="btn" id="collapse-all">Colapsar todo</button>
</div>
</div>
<div class="accordion" id="oferta">
<details class="state" data-text="Aguascalientes">
<summary>
<span class="state-title">
<span>📍 Aguascalientes</span>
<span class="badge">3 planteles</span>
</span>
</summary>
<div class="state-body">
<details class="campus" data-text="Aguascalientes Instituto TecnolÃ³gico de Aguascalientes https://aguascalientes.tecnm.mx/ingenieria-electrica/">
<summary>
<div class="campus-title">
<span>🏫 Instituto Tecnológico de Aguascalientes</span>
<a class="campu

In [38]:
uniInfo = soup.find_all('details', class_='state')


In [39]:
print(uniInfo)

[<details class="state" data-text="Aguascalientes">
<summary>
<span class="state-title">
<span>📍 Aguascalientes</span>
<span class="badge">3 planteles</span>
</span>
</summary>
<div class="state-body">
<details class="campus" data-text="Aguascalientes Instituto TecnolÃ³gico de Aguascalientes https://aguascalientes.tecnm.mx/ingenieria-electrica/">
<summary>
<div class="campus-title">
<span>🏫 Instituto Tecnológico de Aguascalientes</span>
<a class="campus-link" href="https://aguascalientes.tecnm.mx" rel="noopener" target="_blank">Sitio del plantel ↗</a>
</div>
<span class="badge">15 carreras</span>
</summary>
<div class="program-grid">
<div class="card program" data-text="Aguascalientes Instituto TecnolÃ³gico de Aguascalientes IngenierÃ­a ElectrÃ³nica IELC-2010-211 Escolarizada Licenciatura">
<h4>Ingeniería Electrónica</h4>
<div class="meta">
<div><strong>Clave oficial:</strong> IELC-2010-211</div>
<div><strong>Modalidad:</strong> <span class="tag">Escolarizada</span></div>
<div><strong>

In [40]:
for state in uniInfo[:40]:
    print(state['data-text'])


Aguascalientes
Baja California
Baja California Sur
Campeche
Chiapas
Chihuahua
Ciudad de MÃ©xico
Coahuila
Colima
Durango
Estado de MÃ©xico
Guanajuato
Guerrero
Hidalgo
Jalisco
MichoacÃ¡n
Morelos
Nayarit
Nuevo LeÃ³n
Oaxaca
Puebla
QuerÃ©taro
Quintana Roo
San Luis PotosÃ­
Sinaloa
Sonora
Tabasco
Tamaulipas
Tlaxcala
Veracruz
YucatÃ¡n
Zacatecas


In [41]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import time

# URL base
url = 'https://www.tecnm.mx/?vista=Licenciaturas'
response = requests.get(url)
response.encoding = 'utf-8'

# Parse HTML
soup = BeautifulSoup(response.text, 'html.parser')

# Find all states
states = soup.find_all('details', class_='state')

all_data = []

print(f"Found {len(states)} states...\n")

total_campuses = 0
total_programs = 0

# Loop through each state
for s, state in enumerate(states, 1):
    estado = state.get('data-text', 'Sin estado').strip()
    print(f"({s}/{len(states)}) Processing state: {estado}")

    # Find campuses in this state
    campuses = state.find_all('details', class_='campus')
    total_campuses += len(campuses)
    print(f"   Found {len(campuses)} campuses in {estado}")

    for c, campus in enumerate(campuses, 1):
        campus_span = campus.find('span')
        campus_name = campus_span.text.strip() if campus_span else "Sin nombre"

        campus_link_tag = campus.find('a', class_='campus-link')
        campus_link = campus_link_tag['href'].strip() if campus_link_tag else None

        # Find programs (careers)
        programs = campus.find_all('div', class_='card program')
        total_programs += len(programs)
        print(f"      ({c}/{len(campuses)}) Campus: {campus_name} -> {len(programs)} carreras")

        for program in programs:
            carrera = program.find('h4').get_text(strip=True) if program.find('h4') else "Sin carrera"

            meta = program.find('div', class_='meta')
            clave = modalidad = grado = None

            if meta:
                for div in meta.find_all('div'):
                    text = div.get_text(strip=True)
                    if 'Clave oficial:' in text:
                        clave = text.replace('Clave oficial:', '').strip()
                    elif 'Modalidad:' in text:
                        modalidad = text.replace('Modalidad:', '').strip()
                    elif 'Grado:' in text:
                        grado = text.replace('Grado:', '').strip()

            # Career link
            actions = program.find('div', class_='actions')
            career_link_tag = actions.find('a') if actions else None
            career_link = career_link_tag['href'].strip() if career_link_tag else None

            all_data.append({
                'Estado': estado,
                'Nombre del tecnológico': campus_name,
                'Clave oficial': clave,
                'Modalidad': modalidad,
                'Grado que otorga': grado,
                'Carrera': carrera,
                'URL del tecnológico': campus_link,
                'URL de la carrera': career_link
            })

    time.sleep(10)

# Convert to DataFrame
df = pd.DataFrame(all_data)

# Clean text encoding
df = df.replace({
    'Ã¡': 'á', 'Ã©': 'é', 'Ã­': 'í', 'Ã³': 'ó', 'Ãº': 'ú', 'Ã±': 'ñ',
    'Ã': 'Á', 'Ã‰': 'É', 'Ã': 'Í', 'Ã“': 'Ó', 'Ãš': 'Ú', 'Ã‘': 'Ñ',
    'Ãœ': 'Ü', 'Ã¼': 'ü'
}, regex=True)

# Drop duplicates
df = df.drop_duplicates()

# Save to CSV
df.to_csv('tecnmLIC.csv', index=False, encoding='utf-8-sig')

print("\nScraping complete!")
print(f"Total states processed: {len(states)}")
print(f"Total campuses found: {total_campuses}")
print(f"Total careers found: {total_programs}")
print("Saved as tecnmLIC.csv")

# --- Load and display the clean DataFrame ---
df_clean = pd.read_csv('tecnmLIC.csv')

# Optional: show only key columns and the first few rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 100)
display(df_clean.head(10))

print(f"\nPreviewing {len(df_clean)} total rows.")


Found 32 states...

(1/32) Processing state: Aguascalientes
   Found 3 campuses in Aguascalientes
      (1/3) Campus: 🏫 Instituto Tecnológico de Aguascalientes -> 15 carreras
      (2/3) Campus: 🏫 Instituto Tecnológico de Pabellón de Arteaga -> 7 carreras
      (3/3) Campus: 🏫 Instituto Tecnológico El Llano Aguascalientes -> 7 carreras
(2/32) Processing state: Baja California
   Found 3 campuses in Baja California
      (1/3) Campus: 🏫 Instituto Tecnológico de Ensenada -> 12 carreras
      (2/3) Campus: 🏫 Instituto Tecnológico de Mexicali -> 19 carreras
      (3/3) Campus: 🏫 Instituto Tecnológico de Tijuana -> 25 carreras
(3/32) Processing state: Baja California Sur
   Found 4 campuses in Baja California Sur
      (1/4) Campus: 🏫 Instituto Tecnológico de Estudios Superiores de Los Cabos -> 10 carreras
      (2/4) Campus: 🏫 Instituto Tecnológico de La Paz -> 12 carreras
      (3/4) Campus: 🏫 Instituto Tecnológico Superior de Ciudad Constitución -> 11 carreras
      (4/4) Campus: 🏫 Insti

Estado                     Nombre del tecnológico  Clave oficial  \
0  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IELC-2010-211   
1  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IELE-2010-209   
2  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  ICBS-2024-249   
3  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IDAP-2024-246   
4  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IGEM-2009-201   
5  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IGEM-2009-201   
6  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IMAT-2010-222   
7  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  ISEM-2023-244   
8  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  ISIC-2010-224   
9  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  ITIC-2010-225   

         Modalidad Grado que otorga  \
0     Escolarizada     Licenciatura   
1     Escolarizada     Licenciatura   
2     Escolarizada     Licenciatura   
3     Escolarizada     Licenciatura   
4     Escolarizada     Licenciatura   
5  No Escolarizada     Licenciatura   
6     Escolarizada     Licenciatura   
7     Escolarizada     Licenciatura   
8  No Escolarizada     Licenciatura   
9     Escolarizada     Licenciatura   

                                                        Carrera  \
0                                        Ingeniería Electrónica   
1                                          Ingeniería Eléctrica   
2                                  Ingeniería en Ciberseguridad   
3                      Ingeniería en Desarrollo de Aplicaciones   
4                             Ingeniería en Gestión Empresarial   
5                             Ingeniería en Gestión Empresarial   
6                                      Ingeniería en Materiales   
7                                 Ingeniería en Semiconductores   
8                        Ingeniería en Sistemas Computacionales   
9  Ingeniería en Tecnologías de la Información y Comunicaciones   

               URL del tecnológico  \
0  https://aguascalientes.tecnm.mx   
1  https://aguascalientes.tecnm.mx   
2  https://aguascalientes.tecnm.mx   
3  https://aguascalientes.tecnm.mx   
4  https://aguascalientes.tecnm.mx   
5  https://aguascalientes.tecnm.mx   
6  https://aguascalientes.tecnm.mx   
7  https://aguascalientes.tecnm.mx   
8  https://aguascalientes.tecnm.mx   
9  https://aguascalientes.tecnm.mx   

                                                                            URL de la carrera  
0                                     https://aguascalientes.tecnm.mx/ingenieria-electronica/  
1                                       https://aguascalientes.tecnm.mx/ingenieria-electrica/  
2                               https://aguascalientes.tecnm.mx/ingenieria-en-ciberseguridad/  
3                   https://aguascalientes.tecnm.mx/ingenieria-en-desarrollo-de-aplicaciones/  
4                          https://aguascalientes.tecnm.mx/ingenieria-en-gestion-empresarial/  
5                          https://aguascalientes.tecnm.mx/ingenieria-en-gestion-empresarial/  
6                                   https://aguascalientes.tecnm.mx/ingenieria-en-materiales/  
7                              https://aguascalientes.tecnm.mx/ingenieria-en-semiconductores/  
8                                                             https://aguascalientes.tecnm.mx  
9  https://aguascalientes.tecnm.mx/ingenieria-en-tecnologia-de-la-informacion-comunicaciones/


Previewing 2450 total rows.


In [42]:
import pandas as pd

# Load your CSV
df = pd.read_csv("tecnmLIC.csv")

# View first few rows and columns
print(df.head())
print(df.info())


           Estado                     Nombre del tecnológico  Clave oficial  \
0  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IELC-2010-211   
1  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IELE-2010-209   
2  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  ICBS-2024-249   
3  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IDAP-2024-246   
4  Aguascalientes  🏫 Instituto Tecnológico de Aguascalientes  IGEM-2009-201   

      Modalidad Grado que otorga                                   Carrera  \
0  Escolarizada     Licenciatura                    Ingeniería Electrónica   
1  Escolarizada     Licenciatura                      Ingeniería Eléctrica   
2  Escolarizada     Licenciatura              Ingeniería en Ciberseguridad   
3  Escolarizada     Licenciatura  Ingeniería en Desarrollo de Aplicaciones   
4  Escolarizada     Licenciatura         Ingeniería en Gestión Empresarial   

               URL del tecnológico  \
0  https://aguasca

In [43]:
import pandas as pd
import re

# Load the CSV file
df = pd.read_csv("tecnmLIC.csv")

# Function to clean text: remove emojis, fix encoding, normalize spaces
def clean_text(text):
    if isinstance(text, str):
        # Fix typical bad encodings (mojibake) e.g., Ã© → é
        text = (text.encode('latin1', 'ignore')
                    .decode('utf-8', 'ignore')
                    .encode('utf-8', 'ignore')
                    .decode('utf-8', 'ignore'))
        
        # Remove emojis and non-ASCII characters except accented letters
        text = re.sub(r'[^\w\sÁÉÍÓÚáéíóúÑñüÜ.,;:()\-–]+', '', text)
        # Normalize multiple spaces
        text = re.sub(r'\s+', ' ', text).strip()
        return text
    return text

# Apply cleaning to all string columns
for col in df.select_dtypes(include=['object']).columns:
    df[col] = df[col].apply(clean_text)

# Preview cleaned data
df.head()



Estado                  Nombre del tecnológico  Clave oficial  \
0  Aguascalientes  Instituto Tecnolgico de Aguascalientes  IELC-2010-211   
1  Aguascalientes  Instituto Tecnolgico de Aguascalientes  IELE-2010-209   
2  Aguascalientes  Instituto Tecnolgico de Aguascalientes  ICBS-2024-249   
3  Aguascalientes  Instituto Tecnolgico de Aguascalientes  IDAP-2024-246   
4  Aguascalientes  Instituto Tecnolgico de Aguascalientes  IGEM-2009-201   

      Modalidad Grado que otorga                                  Carrera  \
0  Escolarizada     Licenciatura                     Ingeniera Electrnica   
1  Escolarizada     Licenciatura                       Ingeniera Elctrica   
2  Escolarizada     Licenciatura              Ingeniera en Ciberseguridad   
3  Escolarizada     Licenciatura  Ingeniera en Desarrollo de Aplicaciones   
4  Escolarizada     Licenciatura          Ingeniera en Gestin Empresarial   

             URL del tecnológico  \
0  https:aguascalientes.tecnm.mx   
1  https:aguascalientes.tecnm.mx   
2  https:aguascalientes.tecnm.mx   
3  https:aguascalientes.tecnm.mx   
4  https:aguascalientes.tecnm.mx   

                                                       URL de la carrera  
0                    https:aguascalientes.tecnm.mxingenieria-electronica  
1                      https:aguascalientes.tecnm.mxingenieria-electrica  
2              https:aguascalientes.tecnm.mxingenieria-en-ciberseguridad  
3  https:aguascalientes.tecnm.mxingenieria-en-desarrollo-de-aplicaciones  
4         https:aguascalientes.tecnm.mxingenieria-en-gestion-empresarial

In [ ]:
print(df.isna().sum())  # See which columns have missing data
print(df.describe(include='object'))  # Summary of text columns


In [44]:
df.to_csv("universidades_clean.csv", index=False)
print("Cleaned CSV universidades_clean.csv")


Cleaned CSV universidades_clean.csv


In [45]:
import pandas as pd
import json

# Load CSV
df = pd.read_csv("universidades_clean.csv", encoding="utf-8")

# Optional: Replace NaN with None so MongoDB interprets them as null
df = df.where(pd.notnull(df), None)

# Convert to list of dictionaries (records)
data = df.to_dict(orient="records")

# Save to JSON
with open("universidades_clean.json", "w", encoding="utf-8") as f:
    json.dump(data, f, ensure_ascii=False, indent=4)

print(f" JSON file created successfully! Total records: {len(data)}")


 JSON file created successfully! Total records: 2450
